In [33]:
import os
import sys
module_path = os.path.abspath(os.path.join('../trading-bot'))
if module_path not in sys.path:
    sys.path.append(module_path)

In [34]:
import pandas as pd
import numpy as np

from plotly import tools
from plotly.subplots import make_subplots
from plotly.offline import init_notebook_mode, iplot
init_notebook_mode(connected=True)
import plotly.graph_objs as go
import chart_studio.plotly.plotly as py
import gc

import matplotlib.pyplot as plt
import seaborn as sns

In [35]:
df = pd.read_csv("../resources/Bitstamp_BTCUSD_2021_minute.csv", skiprows=1)
df.drop(['date', 'symbol'], axis=1, inplace=True)
df.columns = ["unixtimestamp_millis", "open", "high", "low", "close", "volume_btc", "volume_usd"]
df["unixtimestamp_millis"] = df["unixtimestamp_millis"] * 1000
df.insert(loc=0, column='datetime', value=pd.to_datetime(df['unixtimestamp_millis'], unit='ms'))
df = df.iloc[::-1]
df.set_index("datetime", inplace=True)
df = df.resample("5T").agg({"unixtimestamp_millis": "first",
                                        "open":  "first",
                                        "high":  "max",
                                        "low":   "min",
                                        "close": "last",
                                        "volume_btc": "sum",
                                        "volume_usd": "sum"
                                    })
df.reset_index(inplace=True)
df["datetime"] = df["datetime"].shift(-1)
df["unixtimestamp_millis"] = df["unixtimestamp_millis"].shift(-1)
df = df[:-1]
df = df.astype({"unixtimestamp_millis": np.int64, "volume_btc": np.int64, "volume_usd": np.int64})
df

datetime  unixtimestamp_millis      open      high       low  \
0     2021-01-01 00:05:00         1609459500000  29007.31  29086.90  29007.31   
1     2021-01-01 00:10:00         1609459800000  29021.86  29025.68  28910.15   
2     2021-01-01 00:15:00         1609460100000  28932.99  28945.01  28774.64   
3     2021-01-01 00:20:00         1609460400000  28812.07  28916.52  28800.92   
4     2021-01-01 00:25:00         1609460700000  28893.72  28919.39  28802.97   
...                   ...                   ...       ...       ...       ...   
99492 2021-12-12 11:05:00         1639307100000  48964.56  49036.99  48933.56   
99493 2021-12-12 11:10:00         1639307400000  48890.17  48957.32  48866.09   
99494 2021-12-12 11:15:00         1639307700000  48930.55  49017.38  48930.27   
99495 2021-12-12 11:20:00         1639308000000  48958.00  49030.27  48950.01   
99496 2021-12-12 11:25:00         1639308300000  49009.28  49108.82  49009.28   

          close  volume_btc  volume_usd  
0      29045.19          21      617118  
1      28937.66           8      259818  
2      28834.74          40     1166077  
3      28916.52          10      303865  
4      28907.28          16      465005  
...         ...         ...         ...  
99492  48933.56           0       23694  
99493  48937.44           2      122581  
99494  48944.30           0       40578  
99495  49010.31           1       57165  
99496  49057.92           3      183251  

[99497 rows x 8 columns]

In [36]:
df_bt_res = pd.read_csv("../resources/reports/report.csv", sep=",")
df_bt_res.insert(loc=0, column='datetime', value=pd.to_datetime(df_bt_res['timestamp_millis'], unit='ms'))
df_bt_res.head()

datetime  timestamp_millis       btc       overall
0 2021-01-03 02:30:00     1609641000000  0.003065  50000.000000
1 2021-01-03 05:30:00     1609651800000  0.003012  50001.784976
2 2021-01-03 09:00:00     1609664400000  0.002905  50009.216631
3 2021-01-03 12:30:00     1609677000000  0.002905  50009.199745
4 2021-01-03 16:00:00     1609689600000  0.003024  49993.092920

In [37]:
df.dtypes

datetime                datetime64[ns]
unixtimestamp_millis             int64
open                           float64
high                           float64
low                            float64
close                          float64
volume_btc                       int64
volume_usd                       int64
dtype: object

In [38]:
df_price = pd.merge(df_bt_res, df, on="datetime", how='left')
df_buy = df_price[df_price["btc"] > 0]
df_sell = df_price[df_price["btc"] < 0]

In [39]:
df_buy

datetime  timestamp_millis       btc       overall  \
0    2021-01-03 02:30:00     1609641000000  0.003065  50000.000000   
1    2021-01-03 05:30:00     1609651800000  0.003012  50001.784976   
2    2021-01-03 09:00:00     1609664400000  0.002905  50009.216631   
3    2021-01-03 12:30:00     1609677000000  0.002905  50009.199745   
4    2021-01-03 16:00:00     1609689600000  0.003024  49993.092920   
...                  ...               ...       ...           ...   
1438 2021-12-11 17:30:00     1639243800000  0.002039  50131.250402   
1439 2021-12-11 21:00:00     1639256400000  0.002058  50127.501429   
1440 2021-12-12 00:30:00     1639269000000  0.002023  50136.111933   
1441 2021-12-12 04:00:00     1639281600000  0.002033  50133.377008   
1442 2021-12-12 07:30:00     1639294200000  0.002033  50133.309024   

      unixtimestamp_millis      open      high       low     close  \
0            1609641000000  32760.95  32830.00  32760.95  32796.12   
1            1609651800000  33864.96  34075.98  33850.01  33972.81   
2            1609664400000  34489.50  34531.16  34302.59  34380.28   
3            1609677000000  34274.78  34364.46  34261.63  34321.97   
4            1609689600000  33592.25  33700.00  33548.84  33557.89   
...                    ...       ...       ...       ...       ...   
1438         1639243800000  48971.36  48976.03  48920.56  48962.70   
1439         1639256400000  48681.33  48708.91  48568.93  48593.31   
1440         1639269000000  49615.68  49659.03  49567.55  49642.00   
1441         1639281600000  49325.95  49361.49  49314.88  49341.61   
1442         1639294200000  49228.43  49378.99  49228.43  49349.43   

      volume_btc  volume_usd  
0             16      535233  
1             55     1885454  
2             35     1225408  
3             10      348167  
4             23      785766  
...          ...         ...  
1438           0       11072  
1439           2      129426  
1440           0       11734  
1441           1       56391  
1442           3      192119  

[1162 rows x 11 columns]

In [40]:
df_sell

datetime  timestamp_millis       btc       overall  \
5    2021-01-03 19:30:00     1609702200000 -0.014911  49988.453791   
7    2021-01-04 09:30:00     1609752600000 -0.003002  49984.602959   
11   2021-01-05 10:00:00     1609840800000 -0.009542  49984.875207   
19   2021-01-06 16:30:00     1609950600000 -0.020575  49998.255452   
30   2021-01-08 06:00:00     1610085600000 -0.026604  50019.786099   
...                  ...               ...       ...           ...   
1416 2021-12-05 17:30:00     1638725400000 -0.012173  50135.388746   
1418 2021-12-06 08:30:00     1638779400000 -0.002036  50134.138856   
1426 2021-12-07 21:00:00     1638910800000 -0.013791  50130.890528   
1429 2021-12-09 05:30:00     1639027800000 -0.003951  50127.882654   
1434 2021-12-10 22:00:00     1639173600000 -0.008271  50127.742798   

      unixtimestamp_millis      open      high       low     close  \
5            1609702200000  32641.00  32686.96  32557.90  32632.63   
7            1609752600000  31655.09  31684.89  31450.00  31497.99   
11           1609840800000  31601.26  31630.76  31490.00  31573.13   
19           1609950600000  34965.82  35063.42  34858.79  34892.16   
30           1610085600000  37985.50  38091.89  37926.28  37988.78   
...                    ...       ...       ...       ...       ...   
1416         1638725400000  48906.69  49183.36  48812.23  49112.91   
1418         1638779400000  48063.70  48292.88  47920.01  48259.87   
1426         1638910800000  50309.89  50518.35  50303.71  50452.69   
1429         1639027800000  49781.51  49800.62  49726.30  49790.14   
1434         1639173600000  47999.48  48111.50  47946.33  47950.67   

      volume_btc  volume_usd  
5             43     1409685  
7             79     2518872  
11            33     1053614  
19            47     1664938  
30            23      901586  
...          ...         ...  
1416          25     1238948  
1418          20      989229  
1426           3      201089  
1429          21     1057051  
1434           6      294968  

[281 rows x 11 columns]

In [51]:
overall_trace = go.Scatter(
    x = df_bt_res['datetime'],
    y = df_bt_res['overall'].astype(float),
    mode = 'lines',
    name = 'Capital'
)


buy_trace = go.Scatter(
    x = df_buy['datetime'],
    y = df_buy['open'].astype(float),
    mode='markers',
    name = 'Buy'
)

sell_trace = go.Scatter(
    x = df_sell['datetime'],
    y = df_sell['open'].astype(float),
    mode='markers',
    name = 'Sell'
)

price_trace = go.Scatter(
    x = df['datetime'],
    y = df['open'].astype(float),
    mode = 'lines',
    name = 'Open'
)

layout = dict(
    title='Bitcoin Prices vs Agent performance',
    xaxis=dict(
        rangeselector=dict(
            buttons=list([
                #change the count to desired amount of months.
                dict(count=1,
                     label='1m',
                     step='month',
                     stepmode='backward'),
                dict(count=6,
                     label='6m',
                     step='month',
                     stepmode='backward'),
                dict(count=12,
                     label='1y',
                     step='month',
                     stepmode='backward'),
                dict(count=36,
                     label='3y',
                     step='month',
                     stepmode='backward'),
                dict(step='all')
            ])
        ),
        rangeslider=dict(
            visible = True
        ),
        type='date'
    )
)

fig = make_subplots(specs=[[{"secondary_y": True}]])
fig.add_trace(
    overall_trace,
    secondary_y=False,
)

fig.add_trace(
    price_trace,
    secondary_y=True,
)

fig.add_trace(
    buy_trace,
    secondary_y=True,
)

fig.add_trace(
    sell_trace,
    secondary_y=True,
)

fig.update_layout(layout)